# <STRONG> 1) Collecting and Storing data

In [1]:
# Import libraries
import json
import requests
import pandas as pd
from pandas import json_normalize
import warnings

# Set config to jupyter
pd.set_option('display.max_columns', None)
warnings.filterwarnings('ignore')

In [2]:
# Assuming chromecast as main serach and other 4 terms (possible competitors in Media Streaming) to enrich the analysis
streaming_devics_list = [
    'chromecast',
    'fire%20tv%20stick',
    'apple%20tv',
    'roku',
    'google%20home'
]

# Creating a function to get max 500 itens of each media streaming device
def fetch_results(search_query, max_results=500):
    url_base = "https://api.mercadolibre.com/sites/MLA/search"
    limit = 50
    results = []

    # Using request to find the total in pagination for that device
    response = requests.get(f"{url_base}?q={search_query}&limit={limit}&offset=0")
    if response.status_code == 200:
        data = response.json()
        total_available = data['paging']['total']
        print(f'{search_query} Total Available: {total_available}')
        
        # Adjusting max_result
        max_results = min(max_results, total_available)
        
        # Adding the first result of request
        results.extend(data['results'])

        # Calculating how many other requests will be needed
        requests_needed = (max_results - len(data['results'])) // limit

        for i in range(1, requests_needed + 1):
            offset = i * limit
            if len(results) >= max_results:
                break
            response = requests.get(f"{url_base}?q={search_query}&limit={limit}&offset={offset}")
            if response.status_code == 200:
                data = response.json()
                results.extend(data['results'])
            else:
                print("Request ERROR :", response.status_code)
                break
    else:
        print("Initial request ERROR:", response.status_code)
        return None

    df = json_normalize(results)
    df['search_word'] = search_query
    df['search_word'] = df['search_word'].str.replace('%20', ' ')
    
    return df

# Creating a function to apply "fetch_results() in each device from device list"
def fetch_multiple_devices(device_list):
    full_df = pd.DataFrame()

    # iterate in streaming devices list
    for device in device_list:
        df_device = fetch_results(device)
        if df_device is not None:
            full_df = pd.concat([full_df, df_device], ignore_index=True)
        else:
            print(f"Fail to get results for : {device}")

    return full_df

# Applying and displaying
df = fetch_multiple_devices(streaming_devics_list)
df

chromecast Total Available: 312
fire%20tv%20stick Total Available: 99
apple%20tv Total Available: 113
roku Total Available: 286
google%20home Total Available: 68


id                                              title  \
0    MLA1438429679  Chromecast Google Ga03131 Tv Hd 8gb 2gb Ram 60...   
1    MLA1747863456  Chromecast Google Ga03131 Tv Hd 8gb 2gb Ram 60...   
2    MLA1862361768  Google Chromecast 4 Generación Con Google Tv H...   
3    MLA1642551802  Google Chromecast 3 Full Hd Media Streaming Negro   
4    MLA1403394039  Google Chromecast With Google Tv Ga01919-us De...   
..             ...                                                ...   
730  MLA1432597373  Usado Google Home Mini Google Assistant Coral ...   
731  MLA1361528507  Parlante Inteligente Google Home Mini Smart Sp...   
732  MLA1854015610              Google Home Mini Con Google Assistant   
733  MLA1859560674  Google Home Mini Assist Asistente Virtual Chal...   
734  MLA1641133866  Google Home Mini Asistente Virtual Google Assi...   

    condition                  thumbnail_id catalog_product_id  \
0         new  891351-MLU74085599976_012024        MLA21237756   
1         new  652735-MLC52874645029_122022        MLA21815165   
2         new  827368-MLU74338205859_022024        MLA24460156   
3         new  978472-MEC32125652047_092019        MLA20544894   
4         new  898046-MLA74652414632_022024        MLA16233187   
..        ...                           ...                ...   
730      used  990282-MLA76780573308_062024        MLA15541914   
731      used  868814-MLA54199330242_032023        MLA15541914   
732      used  653453-MLA77635406086_072024        MLA15541914   
733      used  835602-MLA77740107922_072024        MLA15541914   
734      used  600981-MLU72605014728_112023        MLA15541914   

    listing_type_id                                    sanitized_title  \
0      gold_special  chromecast-google-ga03131-tv-hd-8gb-2gb-ram-60...   
1          gold_pro  chromecast-google-ga03131-tv-hd-8gb-2gb-ram-60...   
2          gold_pro  google-chromecast-4-generacion-con-google-tv-h...   
3      gold_special  google-chromecast-3-full-hd-media-streaming-negro   
4          gold_pro  google-chromecast-with-google-tv-ga01919-us-de...   
..              ...                                                ...   
730        gold_pro  usado-google-home-mini-google-assistant-coral-...   
731        gold_pro                                                      
732    gold_special              google-home-mini-con-google-assistant   
733    gold_special  google-home-mini-assist-asistente-virtual-chal...   
734    gold_special  google-home-mini-asistente-virtual-google-assi...   

                                             permalink buying_mode site_id  \
0    https://www.mercadolibre.com.ar/chromecast-goo...  buy_it_now     MLA   
1    https://www.mercadolibre.com.ar/chromecast-goo...  buy_it_now     MLA   
2    https://www.mercadolibre.com.ar/google-chromec...  buy_it_now     MLA   
3    https://www.mercadolibre.com.ar/google-chromec...  buy_it_now     MLA   
4    https://www.mercadolibre.com.ar/google-chromec...  buy_it_now     MLA   
..                                                 ...         ...     ...   
730  https://articulo.mercadolibre.com.ar/MLA-14325...  buy_it_now     MLA   
731  https://articulo.mercadolibre.com.ar/MLA-13615...  buy_it_now     MLA   
732  https://articulo.mercadolibre.com.ar/MLA-18540...  buy_it_now     MLA   
733  https://articulo.mercadolibre.com.ar/MLA-18595...  buy_it_now     MLA   
734  https://articulo.mercadolibre.com.ar/MLA-16411...  buy_it_now     MLA   

    category_id                    domain_id  \
0     MLA352001  MLA-STREAMING_MEDIA_DEVICES   
1     MLA352001  MLA-STREAMING_MEDIA_DEVICES   
2     MLA352001  MLA-STREAMING_MEDIA_DEVICES   
3     MLA352001  MLA-STREAMING_MEDIA_DEVICES   
4     MLA352001  MLA-STREAMING_MEDIA_DEVICES   
..          ...                          ...   
730   MLA409415           MLA-SMART_SPEAKERS   
731   MLA409415           MLA-SMART_SPEAKERS   
732   MLA409415           MLA-SMART_SPEAKERS   
733   MLA409415           MLA-SMART_SPEA

In [3]:
# Investigating attribute
df['attributes'][0]

[{'id': 'BRAND',
  'name': 'Marca',
  'value_id': '52701',
  'value_name': 'Google',
  'attribute_group_id': 'OTHERS',
  'attribute_group_name': 'Otros',
  'value_struct': None,
  'values': [{'id': '52701', 'name': 'Google', 'struct': None, 'source': 1}],
  'source': 1,
  'value_type': 'string'},
 {'id': 'COLOR',
  'name': 'Color',
  'value_id': '52055',
  'value_name': 'Blanco',
  'attribute_group_id': 'OTHERS',
  'attribute_group_name': 'Otros',
  'value_struct': None,
  'values': [{'id': '52055', 'name': 'Blanco', 'struct': None, 'source': 1}],
  'source': 1,
  'value_type': 'string'},
 {'id': 'GTIN',
  'name': 'Código universal de producto',
  'value_id': None,
  'value_name': '810037290042',
  'attribute_group_id': 'OTHERS',
  'attribute_group_name': 'Otros',
  'value_struct': None,
  'values': [{'id': None,
    'name': '810037290042',
    'struct': None,
    'source': 6402814585011704}],
  'source': 6402814585011704,
  'value_type': 'string'},
 {'id': 'ITEM_CONDITION',
  'name': 

In [5]:
# Investigating the results of item API
Item_Id = 'MLA1438429679'
response_item = requests.get(f'https://api.mercadolibre.com/items/{Item_Id}')

response_item.json()

{'id': 'MLA1438429679',
 'site_id': 'MLA',
 'title': 'Chromecast Google Ga03131 Tv Hd 8gb 2gb Ram 60 Fps Wifi Bluetooth Hdmi 4ta Gen Blanco',
 'seller_id': 310173310,
 'category_id': 'MLA352001',
 'official_store_id': None,
 'price': 112799,
 'base_price': 112799,
 'original_price': None,
 'currency_id': 'ARS',
 'initial_quantity': 2596,
 'sale_terms': [{'id': 'WARRANTY_TYPE',
   'name': 'Tipo de garantía',
   'value_id': '2230279',
   'value_name': 'Garantía de fábrica',
   'value_struct': None,
   'values': [{'id': '2230279',
     'name': 'Garantía de fábrica',
     'struct': None}],
   'value_type': 'list'},
  {'id': 'WARRANTY_TIME',
   'name': 'Tiempo de garantía',
   'value_id': None,
   'value_name': '6 meses',
   'value_struct': {'number': 6, 'unit': 'meses'},
   'values': [{'id': None,
     'name': '6 meses',
     'struct': {'number': 6, 'unit': 'meses'}}],
   'value_type': 'number_unit'},
  {'id': 'INVOICE',
   'name': 'Facturación',
   'value_id': '6891885',
   'value_name': 

### Proceeding without retrieving additional data from the second API, as the data needed has already been obtained from the first API.

# <STRONG> 2) Cleaning and Preparing Data

In [4]:
# Keeping just a few columns from previous dataframe df
df2 = df[['id', 'title', 'search_word', 'condition', 'listing_type_id', 'category_id', 'domain_id', 'price', 'available_quantity', 'attributes', 'shipping.free_shipping', 'seller.id', 'seller.nickname']]


# Extracting a few columns from 'attributes' column
def extract_specific_attributes(attributes):
    attribute_dict = {}
    for attribute in attributes:
        if attribute['id'] in ['BRAND', 'GTIN', 'WEIGHT']:
            attribute_dict[attribute['id']] = attribute['value_name']
    return pd.Series(attribute_dict)


attributes_df = df2['attributes'].apply(extract_specific_attributes)

# Concatenating with main dataframe
df_final = pd.concat([df2.drop(columns=['attributes']), attributes_df], axis=1)
df_final

id                                              title  \
0    MLA1438429679  Chromecast Google Ga03131 Tv Hd 8gb 2gb Ram 60...   
1    MLA1747863456  Chromecast Google Ga03131 Tv Hd 8gb 2gb Ram 60...   
2    MLA1862361768  Google Chromecast 4 Generación Con Google Tv H...   
3    MLA1642551802  Google Chromecast 3 Full Hd Media Streaming Negro   
4    MLA1403394039  Google Chromecast With Google Tv Ga01919-us De...   
..             ...                                                ...   
730  MLA1432597373  Usado Google Home Mini Google Assistant Coral ...   
731  MLA1361528507  Parlante Inteligente Google Home Mini Smart Sp...   
732  MLA1854015610              Google Home Mini Con Google Assistant   
733  MLA1859560674  Google Home Mini Assist Asistente Virtual Chal...   
734  MLA1641133866  Google Home Mini Asistente Virtual Google Assi...   

     search_word condition listing_type_id category_id  \
0     chromecast       new    gold_special   MLA352001   
1     chromecast       new        gold_pro   MLA352001   
2     chromecast       new        gold_pro   MLA352001   
3     chromecast       new    gold_special   MLA352001   
4     chromecast       new        gold_pro   MLA352001   
..           ...       ...             ...         ...   
730  google home      used        gold_pro   MLA409415   
731  google home      used        gold_pro   MLA409415   
732  google home      used    gold_special   MLA409415   
733  google home      used    gold_special   MLA409415   
734  google home      used    gold_special   MLA409415   

                       domain_id     price  available_quantity  \
0    MLA-STREAMING_MEDIA_DEVICES  112799.0                 500   
1    MLA-STREAMING_MEDIA_DEVICES  122771.0                 250   
2    MLA-STREAMING_MEDIA_DEVICES  126730.0                   1   
3    MLA-STREAMING_MEDIA_DEVICES  114999.0                   1   
4    MLA-STREAMING_MEDIA_DEVICES  159999.0                   1   
..                           ...       ...                 ...   
730           MLA-SMART_SPEAKERS   66990.0                 500   
731           MLA-SMART_SPEAKERS   79990.0                   1   
732           MLA-SMART_SPEAKERS   55000.0                   1   
733           MLA-SMART_SPEAKERS   40000.0                   1   
734           MLA-SMART_SPEAKERS   50000.0                   1   

     shipping.free_shipping   seller.id                seller.nickname  \
0                      True   310173310                      GLOBAL UP   
1                      True     3135574              MAGAZZINO ALMACEN   
2                      True      680515          ALTAVISTA COMPUTACION   
3                      True  1634953268                    EMOODMARKET   
4                      True   167338436                NOVAINFOEXPRESS   
..                      ...         ...                            ...   
730                    True   284824585                    SKY- VISION   
731                   False   309453406       CAMUS ELECTRONICA.COM.AR   
732                   False  1049472925  CONTRISTANOBLAS20220101203158   
733                   False    57608634                         ROD728   
734                   False   778112200                BUDASSI ESTEBAN   

      BRAND           GTIN    WEIGHT  
0    Google   810037290042      1 kg  
1    Google   810037290042  0.063 kg  
2    Google   810037290042     112 g  
3    Google  4805726470214      40 g  
4    Google   193575007243     0.3 g  
..      ...            ...       ...  
730  Google            NaN     173 g  
731  Google            NaN     173 g  
732  Google            NaN     173 g  
733  Google            NaN     173 g  
734  Google   004277610214     173 g  

[735 rows x 15 columns]

# <STRONG> 3) Analyzing and Generating Insights

#### <div style="color:dodgerblue;"> 3.1) Available Quantity by Domain_id and Search_word </div>
##### Question: How many items are available for each search_word by domain_id?
##### Value: Helps identify the stock levels for different product categories and search terms, guiding inventory management and marketing strategies. 

#### <div style="color:dodgerblue;"> 3.2) Product Condition by Listing Type ID  </div>
##### Question: How many products are new or used by listing_type_id?
##### Value: Understands the distribution of product conditions across different seller tiers, aiding in targeting strategies.

#### <div style="color:dodgerblue;"> 3.3) Free Shipping by Listing Type ID  </div>
##### Question: How many products offer free shipping by listing_type_id?
##### Value: Determines the prevalence of free shipping offers among different seller tiers, helping optimize shipping policies.

#### <div style="color:dodgerblue;"> 3.4) Price Statistics by Search Word and Listing Type ID  </div>
##### Question: What are the minimum, maximum and average prices for each search word, broken down by listing type ID?
##### Value: Provides insights into pricing strategies across different search terms and seller tiers, helping in competitive pricing.

#### <div style="color:dodgerblue;"> 3.5) Top Sellers by Listings for Each Search Word </div>
##### Question: Who are the top 10 sellers with the most listings for each search word?
##### Value: Identifies key sellers for specific search terms, helping in seller relationship management and promotional efforts.

#### <div style="color:dodgerblue;"> 3.6) Price Comparison with and without Free Shipping </div>
##### Question: What are the minimum, maximum, and average prices for each search word with and without free shipping?
##### Value: Understands the pricing impact of free shipping, helping in promotional and pricing strategies.

#### <div style="color:dodgerblue;"> 3.7) Price Comparison by Brand </div>
##### Question: What are the minimum, maximum, and average prices for each search word by brand?
##### Value: Analyzes price variations among different brands, guiding brand positioning and pricing decisions.

#### <div style="color:dodgerblue;"> 3.8) Price Comparison by Condition </div>
##### Question: What are the minimum, maximum, and average prices for each search word by product condition (new, used)?
##### Value: Understands how product condition affects pricing, aiding in pricing strategies for new vs. used products.

#### <div style="color:dodgerblue;"> 3.9) Top Sellers by Available Quantity for Each Search Word </div>
##### Question: Who are the top 5 sellers with the most available quantity for each search word?
##### Value: Identifies sellers with significant stock levels, helping in inventory planning and seller engagement.

# <STRONG> 4) Exporting as CSV

In [25]:
df_final.to_csv('dash_souce.csv', index=False)